**Addi**

**Take Home Exercise**

By: Maria Camila Ortiz

**Business Case**

 In this test, you will build a recommendation system for an E-commerce platform. For 
the design of the recommender, we are giving you two different datasets (the 
datasets are not related, therefore there is no key to join them):

* Amazon Product description: 
https://www.kaggle.com/datasets/promptcloud/amazon-product-dataset-2020

* History purchases of clients: 
https://www.kaggle.com/datasets/mkechinov/ecommerce-purchase-history-from
electronics-store

The final output should be the top 10 recommended products by each client.


 **Requirements**

* Present your analytical solution in a clear way. Please, include why you chose a specific approach, in each stage of the project: Business Understanding, EDA, Feature Engineering, Design of the model, modeling, validation, and showcasing 
the results)

* The product manager also wants to know if you can find new categories apart from the Category column. Hint: You can use the text data such as the columns:  about_product , and 
product_specification .

* Could you define audiences of clients taking into account the output of the 
recommender system? Hint: You can use a clustering approach with the 
recommended products, or use another one that you think is better. Note: audience definition: a group of clients most likely to be receptive to messaging for a particular product or service.

* Design the validation approach for your recommender system, are your 
recommended products good enough for the clients? Hint: Propose some 
metrics or an experiment design


**Optional**
* Given an existing product recommendation system, how do you design an A/B test to improve the system? 

* How would you scale the recommendation system? Hint: Just mention 
some tools or architectural approaches

In [73]:
# Importing libraries
import pandas as pd 
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import plotly.express as px


In [74]:
# Reading eccommerce dataset 
df_ec = pd.read_csv('./data/kz.csv')

### Ecommerce Dataset Exploratory Data Analysis (EDA)

In [75]:
df_ec.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2633521 entries, 0 to 2633520
Data columns (total 8 columns):
 #   Column         Dtype  
---  ------         -----  
 0   event_time     object 
 1   order_id       int64  
 2   product_id     int64  
 3   category_id    float64
 4   category_code  object 
 5   brand          object 
 6   price          float64
 7   user_id        float64
dtypes: float64(3), int64(2), object(3)
memory usage: 160.7+ MB


In [76]:
df_ec.head()

event_time             order_id           product_id  \
0  2020-04-24 11:50:39 UTC  2294359932054536986  1515966223509089906   
1  2020-04-24 11:50:39 UTC  2294359932054536986  1515966223509089906   
2  2020-04-24 14:37:43 UTC  2294444024058086220  2273948319057183658   
3  2020-04-24 14:37:43 UTC  2294444024058086220  2273948319057183658   
4  2020-04-24 19:16:21 UTC  2294584263154074236  2273948316817424439   

    category_id                category_code    brand   price       user_id  
0  2.268105e+18           electronics.tablet  samsung  162.01  1.515916e+18  
1  2.268105e+18           electronics.tablet  samsung  162.01  1.515916e+18  
2  2.268105e+18  electronics.audio.headphone   huawei   77.52  1.515916e+18  
3  2.268105e+18  electronics.audio.headphone   huawei   77.52  1.515916e+18  
4  2.268105e+18                          NaN  karcher  217.57  1.515916e+18

In [77]:
# Nulls percentage for each column 
(df_ec.isnull().sum() / len(df_ec)) * 100

event_time        0.000000
order_id          0.000000
product_id        0.000000
category_id      16.402148
category_code    23.246521
brand            19.214010
price            16.402148
user_id          78.577387
dtype: float64

In [78]:
df_ec.describe(include='all')

event_time      order_id    product_id   category_id  \
count                   2633521  2.633521e+06  2.633521e+06  2.201567e+06   
unique                  1316174           NaN           NaN           NaN   
top     1970-01-01 00:33:40 UTC           NaN           NaN           NaN   
freq                      19631           NaN           NaN           NaN   
mean                        NaN  2.361783e+18  1.674080e+18  2.273827e+18   
std                         NaN  1.716538e+16  3.102249e+17  2.353247e+16   
min                         NaN  2.294360e+18  1.515966e+18  2.268105e+18   
25%                         NaN  2.348807e+18  1.515966e+18  2.268105e+18   
50%                         NaN  2.353254e+18  1.515966e+18  2.268105e+18   
75%                         NaN  2.383131e+18  1.515966e+18  2.268105e+18   
max                         NaN  2.388441e+18  2.388434e+18  2.374499e+18   

                 category_code    brand         price       user_id  
count                  2021319  2127516  2.201567e+06  5.641690e+05  
unique                     510    23021           NaN           NaN  
top     electronics.smartphone  samsung           NaN           NaN  
freq                    357682   358928           NaN           NaN  
mean                       NaN      NaN  1.540932e+02  1.515916e+18  
std                        NaN      NaN  2.419421e+02  2.377083e+07  
min                        NaN      NaN  0.000000e+00  1.515916e+18  
25%                        NaN      NaN  1.456000e+01  1.515916e+18  
50%                        NaN      NaN  5.553000e+01  1.515916e+18  
75%                        NaN      NaN  1.967400e+02  1.515916e+18  
max                        NaN      NaN  5.092590e+04  1.515916e+18

In [79]:
# Checking format on event time column 
df_ec['event_time']

0          2020-04-24 11:50:39 UTC
1          2020-04-24 11:50:39 UTC
2          2020-04-24 14:37:43 UTC
3          2020-04-24 14:37:43 UTC
4          2020-04-24 19:16:21 UTC
                    ...           
2633516    2020-11-21 10:10:01 UTC
2633517    2020-11-21 10:10:13 UTC
2633518    2020-11-21 10:10:30 UTC
2633519    2020-11-21 10:10:30 UTC
2633520    2020-11-21 10:10:30 UTC
Name: event_time, Length: 2633521, dtype: object

In [ ]:
# Checking format
print(df_ec['event_time'].dtype)  
print(df_ec['event_time'].head(10))
print(df_ec['event_time'].tail(10)) 

object
0    2020-04-24 11:50:39 UTC
1    2020-04-24 11:50:39 UTC
2    2020-04-24 14:37:43 UTC
3    2020-04-24 14:37:43 UTC
4    2020-04-24 19:16:21 UTC
5    2020-04-26 08:45:57 UTC
6    2020-04-26 09:33:47 UTC
7    2020-04-26 09:33:47 UTC
8    2020-04-26 09:33:47 UTC
9    2020-04-26 09:33:47 UTC
Name: event_time, dtype: object
2633511    2020-11-21 10:05:04 UTC
2633512    2020-11-21 10:06:01 UTC
2633513    2020-11-21 10:08:14 UTC
2633514    2020-11-21 10:08:54 UTC
2633515    2020-11-21 10:08:54 UTC
2633516    2020-11-21 10:10:01 UTC
2633517    2020-11-21 10:10:13 UTC
2633518    2020-11-21 10:10:30 UTC
2633519    2020-11-21 10:10:30 UTC
2633520    2020-11-21 10:10:30 UTC
Name: event_time, dtype: object


In [80]:
# Checking years of purchases before converting event time column
df_ec['event_year'] = df_ec['event_time'].str[:4]  
print(df_ec['event_year'].value_counts())  # Registers per year

event_year
2020    2613890
1970      19631
Name: count, dtype: int64


There are data from 1970 to 2020. It is necessary to take a look on it in the next steps. 

In [81]:
# Converting to datetime, getting only the date, not the hour
df_ec['event_time'] = pd.to_datetime(df_ec['event_time']).dt.date

In [82]:
# Taking a look into the converted column
df_ec['event_time']

0          2020-04-24
1          2020-04-24
2          2020-04-24
3          2020-04-24
4          2020-04-24
              ...    
2633516    2020-11-21
2633517    2020-11-21
2633518    2020-11-21
2633519    2020-11-21
2633520    2020-11-21
Name: event_time, Length: 2633521, dtype: object

In [83]:
# Unique values
df_ec.nunique()

event_time           323
order_id         1435266
product_id         25113
category_id          900
category_code        510
brand              23021
price               2802
user_id            98262
event_year             2
dtype: int64

In [90]:
# Count occurrences of each order_id
order_counts = df_ec['order_id'].value_counts()

# Filter only duplicated order_ids (those appearing more than once)
duplicated_orders = order_counts[order_counts > 1]  

print(f"Total unique order_id: {df_ec['order_id'].nunique()}")
print(f"Total duplicated order_id: {len(duplicated_orders)}")

Total unique order_id: 1435266
Total duplicated order_id: 563515


Assuming some of the duplicated order_id may not have the user_id associated, I will check on it before cleaning that column. 

In [84]:
# User Purchases Distribution
user_purchases = df_ec['user_id'].value_counts()
user_purchases.describe()

count    98262.000000
mean         5.741477
std         26.240578
min          1.000000
25%          1.000000
50%          2.000000
75%          4.000000
max        635.000000
Name: count, dtype: float64

In [86]:
# Taking a look into high purchase users
high_purchase_users = user_purchases[user_purchases > 4]
high_purchase_users

user_id
1.515916e+18    635
1.515916e+18    632
1.515916e+18    584
1.515916e+18    583
1.515916e+18    579
               ... 
1.515916e+18      5
1.515916e+18      5
1.515916e+18      5
1.515916e+18      5
1.515916e+18      5
Name: count, Length: 22573, dtype: int64

User Purchase Distribution:

In [87]:
# Create an interactive boxplot
fig = px.box(
    user_purchases, 
    x=user_purchases, 
    log_x=True,  # Log scale for better visualization
    title="User Purchase Distribution",
    labels={"x": "Number of Purchases"},
    color_discrete_sequence=["#FFB6C1"] 
)

# Show the interactive plot
fig.show()


Taking into account that the median is 2 purchases by client and the upper fence is 8 in the boxplot, every purchase amount bigger than it will be an outlier and is out of the normal behavior. Anyway, it is not possible to confirm that those numbers are corrupted data, because it can simply mean that a user purchases a lot. 

In [91]:
# Select only rows where order_id is duplicated
df_duplicated_orders = df_ec[df_ec['order_id'].isin(duplicated_orders.index)]

# Count how many of these duplicated orders have a user_id assigned
user_associated_orders = df_duplicated_orders['user_id'].notnull().sum()

print(f"Total rows with duplicated order_id: {len(df_duplicated_orders)}")
print(f"Rows with duplicated order_id that have an associated user_id: {user_associated_orders}")


Total rows with duplicated order_id: 1761770
Rows with duplicated order_id that have an associated user_id: 268936


In [92]:
# Group by order_id and check if any row has a user_id
has_user = df_ec.groupby('order_id')['user_id'].apply(lambda x: x.notnull().any())

# Count orders where at least one row has user_id
print(f"Orders with at least one associated user_id: {has_user.sum()} out of {len(has_user)} total orders")

Orders with at least one associated user_id: 400538 out of 1435266 total orders


As the focus of this recommendation system is the user id and it previous purchase behavior, it is really important not to loose information. That's the reason of searching if in the same order id, there are missing user ids. If so, those data are going to be filled. 

In [93]:
# Fill missing user_id within the same order_id
df_ec['user_id'] = df_ec.groupby('order_id')['user_id'].transform(lambda x: x.fillna(method='bfill').fillna(method='ffill'))

C:\Users\camil\AppData\Local\Temp\ipykernel_36396\472133290.py:2: FutureWarning:

Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.



In [95]:
(df_ec.isnull().sum() / len(df_ec)) * 100

event_time        0.000000
order_id          0.000000
product_id        0.000000
category_id      16.402148
category_code    23.246521
brand            19.214010
price            16.402148
user_id          77.265797
event_year        0.000000
dtype: float64

In [96]:
# Checking null values again
df_ec.isna().sum()

event_time             0
order_id               0
product_id             0
category_id       431954
category_code     612202
brand             506005
price             431954
user_id          2034811
event_year             0
dtype: int64

As the algoryhtm will be based on the user id for the top 10 recomendations, each register without this data is not useful. 

In [97]:
# Cleaning registers with null user_id
df_ec_clean = df_ec.dropna(subset=['user_id'])

In [98]:
# Null values in the new df
df_ec_clean.isna().sum()

event_time            0
order_id              0
product_id            0
category_id       34541
category_code    129370
brand             27224
price             34541
user_id               0
event_year            0
dtype: int64

There's a product id, an order id and the event time for each of the registers of the new dataset. 

In [99]:
# New df info
df_ec_clean.info()

<class 'pandas.core.frame.DataFrame'>
Index: 598710 entries, 0 to 2633520
Data columns (total 9 columns):
 #   Column         Non-Null Count   Dtype  
---  ------         --------------   -----  
 0   event_time     598710 non-null  object 
 1   order_id       598710 non-null  int64  
 2   product_id     598710 non-null  int64  
 3   category_id    564169 non-null  float64
 4   category_code  469340 non-null  object 
 5   brand          571486 non-null  object 
 6   price          564169 non-null  float64
 7   user_id        598710 non-null  float64
 8   event_year     598710 non-null  object 
dtypes: float64(3), int64(2), object(4)
memory usage: 45.7+ MB


In [107]:
df_ec_clean['product_id']

0          1515966223509089906
1          1515966223509089906
2          2273948319057183658
3          2273948319057183658
4          2273948316817424439
                  ...         
2633516    1515966223526602848
2633517    1515966223509089282
2633518    1515966223509089917
2633519    2273948184839454837
2633520    1515966223509127566
Name: product_id, Length: 598710, dtype: int64

Taking a look into Product id, Category id and Category code:

In [100]:
df_ec_clean['product_id'].nunique()

21673

In [101]:
df_ec_clean['category_id'].nunique()

829

In [102]:
df_ec_clean['category_code']

0                   electronics.tablet
1                   electronics.tablet
2          electronics.audio.headphone
3          electronics.audio.headphone
4                                  NaN
                      ...             
2633516         electronics.smartphone
2633517         electronics.smartphone
2633518     appliances.personal.scales
2633519                            NaN
2633520     appliances.kitchen.blender
Name: category_code, Length: 598710, dtype: object

In [103]:
df_ec_clean['category_code'].nunique()

356

In [104]:
df_ec_clean[:6]

event_time             order_id           product_id   category_id  \
0  2020-04-24  2294359932054536986  1515966223509089906  2.268105e+18   
1  2020-04-24  2294359932054536986  1515966223509089906  2.268105e+18   
2  2020-04-24  2294444024058086220  2273948319057183658  2.268105e+18   
3  2020-04-24  2294444024058086220  2273948319057183658  2.268105e+18   
4  2020-04-24  2294584263154074236  2273948316817424439  2.268105e+18   
5  2020-04-26  2295716521449619559  1515966223509261697  2.268105e+18   

                 category_code    brand   price       user_id event_year  
0           electronics.tablet  samsung  162.01  1.515916e+18       2020  
1           electronics.tablet  samsung  162.01  1.515916e+18       2020  
2  electronics.audio.headphone   huawei   77.52  1.515916e+18       2020  
3  electronics.audio.headphone   huawei   77.52  1.515916e+18       2020  
4                          NaN  karcher  217.57  1.515916e+18       2020  
5      furniture.kitchen.table  maestro   39.33  1.515916e+18       2020

In [105]:
# Checking category id vs category code behavior
category_check = df_ec_clean.groupby('category_id')['category_code'].nunique()

# Category id with more than one category code
multiple_categories = category_check[category_check > 1]

In [106]:
print(f"Unique category id: {df_ec_clean['category_id'].nunique()}")

Unique category id: 829


In [107]:
# Checking this to be sure that there are different products that can have same category code but not same category id
if not multiple_categories.empty:
    print("Category id with different category code:")
    print(df_ec_clean[df_ec_clean['category_id'].isin(multiple_categories.index)].head(10))

Category id with different category code:
       event_time             order_id           product_id   category_id  \
29396  1970-01-01  2340102799674573516  2273948226103018253  2.374499e+18   
44197  1970-01-01  2348532001214038357  1515966223523303381  2.374499e+18   
45352  1970-01-01  2348532107388650318  1515966223523303334  2.374499e+18   
45353  1970-01-01  2348532107388650318  1515966223523303307  2.374499e+18   
50000  1970-01-01  2348532573661037488  1515966223523303307  2.374499e+18   
50004  1970-01-01  2348532573661037488  1515966223523303304  2.374499e+18   
50089  1970-01-01  2348532578836808658  1515966223523303381  2.374499e+18   
50090  1970-01-01  2348532578836808658  1515966223523303382  2.374499e+18   
50095  1970-01-01  2348532578836808658  2273948186718503447  2.374499e+18   
51689  1970-01-01  2348532722164564659  1515966223523303390  2.374499e+18   

                category_code      brand   price       user_id event_year  
29396    electronics.video.tv     

Category id seems to be a more general number, related itself with the category. But in category code, there is more information than only the category. It seems a string with the first value as the category and the other information specifies about the type of product. 

In [108]:
# Forcing again the conversion and format to event_time column
df_ec_clean['event_time'] = pd.to_datetime(df_ec_clean['event_time'], errors='coerce', format="%Y-%m-%d %H:%M:%S UTC")


C:\Users\camil\AppData\Local\Temp\ipykernel_36396\2069024307.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [109]:
# Create a new column 'year_month' to group data by Year-Month (YYYY-MM format)
df_ec_clean['year_month'] = df_ec_clean['event_time'].dt.to_period('M')

# Count the number of purchases per month
monthly_purchases = df_ec_clean['year_month'].value_counts().sort_index()

# Convert the result to a DataFrame for better visualization
df_monthly = monthly_purchases.reset_index()
df_monthly.columns = ['year_month', 'purchases']
df_monthly['year_month'] = df_monthly['year_month'].astype(str)  # Convert to string for proper plotting

fig = px.line(
    df_monthly, 
    x='year_month', 
    y='purchases', 
    markers=True,  # Add markers to highlight data points
    title="Purchases Trend Over Time (Monthly)",
    labels={'year_month': 'Year-Month', 'purchases': 'Number of Purchases'},
    color_discrete_sequence=["#FFB6C1"] 
)

fig.show()


C:\Users\camil\AppData\Local\Temp\ipykernel_36396\3007861052.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



This data behavior is not useful for the analysis. The registers for 1970 can be an error when downloading the zip file with the original df. So, assuming those data are corrupted, or if they are not, there are more than 50 years until current date, those registers will be droped. 

In [110]:
# Droping registers related to its date
df_ec_clean = df_ec_clean[df_ec_clean['event_time'].dt.year >= 2010]

# Checking df date range
print(df_ec_clean['event_time'].min(), df_ec_clean['event_time'].max())

2020-01-05 00:00:00 2020-11-21 00:00:00


Monthly Purchases for 2020:

In [111]:
# Count the number of purchases per month
monthly_purchases = df_ec_clean['year_month'].value_counts().sort_index()

# Convert the result to a DataFrame for better visualization
df_monthly = monthly_purchases.reset_index()
df_monthly.columns = ['year_month', 'purchases']
df_monthly['year_month'] = df_monthly['year_month'].astype(str)  # Convert to string for proper plotting

fig = px.line(
    df_monthly, 
    x='year_month', 
    y='purchases', 
    markers=True,  # Add markers to highlight data points
    title="Purchases Trend Over Time (Monthly)",
    labels={'year_month': 'Year-Month', 'purchases': 'Number of Purchases'},
    color_discrete_sequence=["#FFB6C1"] 
)

# Display the chart
fig.show()

There's definately an increasing trend of the purchases, related to the month. There could be a relation between black friday with the purchasing behavior of the users in this ecommerce. The increase between june and august could be related to the summer season, the start of the new school year and the vacations. 

Purchases per Brand:

In [ ]:
# Count the number of purchases per brand
brand_purchases = df_ec['brand'].value_counts().reset_index()
brand_purchases.columns = ['brand', 'purchases']  # Rename columns for clarity

# Filter to show only the top brands
top_brands = brand_purchases.head(20)  # Adjust the number as needed

fig = px.bar(
    top_brands, 
    x='brand',  # X-axis represents the brand names
    y='purchases',  # Y-axis represents the number of purchases
    title="Top 20 Brands by Number of Purchases",  # Chart title
    labels={'brand': 'Brand', 'purchases': 'Number of Purchases'},  # Axis labels
    color_discrete_sequence=["#FFB6C1"], 
    text_auto=True 
)

# Show the chart
fig.show()

In the available information, Samsung leaded the purchases for 2020. 

Purchases per Category Code:

In [113]:
# Count purchases per category_code
category_purchases = df_ec_clean['category_code'].value_counts().reset_index()
category_purchases.columns = ['category_code', 'purchases']

fig = px.bar(
    category_purchases,                                                                                                                                                                                                                                                                                                                                                                                                                                     
    x='category_code', 
    y='purchases', 
    title="Purchases by Category Code",
    labels={'category_code': 'Category', 'purchases': 'Number of Purchases'},
    color_discrete_sequence=["#FFB6C1"] 
)

# Rotate x-axis labels for better readability
fig.update_layout(xaxis_tickangle=-45)

# Show the chart
fig.show()


In [114]:
df_ec_clean['category_code']

0                   electronics.tablet
1                   electronics.tablet
2          electronics.audio.headphone
3          electronics.audio.headphone
4                                  NaN
                      ...             
2633516         electronics.smartphone
2633517         electronics.smartphone
2633518     appliances.personal.scales
2633519                            NaN
2633520     appliances.kitchen.blender
Name: category_code, Length: 597290, dtype: object

In [115]:
# Count numerical vs. textual category codes
num_values = df_ec_clean['category_code'].apply(lambda x: str(x).replace('.', '').isdigit()).sum()
text_values = len(df_ec_clean) - num_values

print(f"Text category codes: {text_values}")
print(f"Numeric category codes: {num_values}")

Text category codes: 562862
Numeric category codes: 34428


Due to the small ammount of numerical category codes, those will be dropped out. Numerical codes do not gives us information about the hierarchy in which it seems the category code bases on. 

In [116]:
# Remove numeric category codes
df_ec_clean = df_ec_clean[~df_ec_clean['category_code'].apply(lambda x: str(x).replace('.', '').isdigit())]

In [117]:
df_ec_clean.info()

<class 'pandas.core.frame.DataFrame'>
Index: 562862 entries, 0 to 2633520
Data columns (total 10 columns):
 #   Column         Non-Null Count   Dtype         
---  ------         --------------   -----         
 0   event_time     562862 non-null  datetime64[ns]
 1   order_id       562862 non-null  int64         
 2   product_id     562862 non-null  int64         
 3   category_id    562862 non-null  float64       
 4   category_code  433938 non-null  object        
 5   brand          535699 non-null  object        
 6   price          562862 non-null  float64       
 7   user_id        562862 non-null  float64       
 8   event_year     562862 non-null  object        
 9   year_month     562862 non-null  period[M]     
dtypes: datetime64[ns](1), float64(3), int64(2), object(3), period[M](1)
memory usage: 47.2+ MB


In [118]:
# Count purchases per category_code
category_purchases = df_ec_clean['category_code'].value_counts().reset_index()
category_purchases.columns = ['category_code', 'purchases']

fig = px.bar(
    category_purchases,                                                                                                                                                                                                                                                                                                                                                                                                                                     
    x='category_code', 
    y='purchases', 
    title="Purchases by Category Code",
    labels={'category_code': 'Category', 'purchases': 'Number of Purchases'},
    color_discrete_sequence=["#FFB6C1"] 
)

# Rotate x-axis labels for better readability
fig.update_layout(xaxis_tickangle=-45)

# Show the chart
fig.show()

Smartphone was the most selled category in 2020. 

In [119]:
# Price column analysis
df_ec_clean['price'].describe()

count    562862.000000
mean        208.435114
std         304.600621
min           0.000000
25%          23.130000
50%          87.940000
75%         277.750000
max       18328.680000
Name: price, dtype: float64

In [ ]:
# Define price bins (ranges) based on the statistical distribution
bins = [0, 20, 90, 280, 1000, 5000, df_ec_clean['price'].max()]  # Define price intervals
labels = ['0-20', '20-90', '90-280', '280-1000', '1000-5000', '5000+']  # Labels for each range

# Create a new column assigning each price to a specific range
df_ec_clean['price_range'] = pd.cut(df_ec_clean['price'], bins=bins, labels=labels, include_lowest=True)

# Count the number of purchases in each price range
price_distribution = df_ec_clean['price_range'].value_counts().reset_index()
price_distribution.columns = ['price_range', 'count']  # Rename columns for clarity

# Sort the DataFrame by price range order
price_distribution['price_range'] = pd.Categorical(price_distribution['price_range'], categories=labels, ordered=True)
price_distribution = price_distribution.sort_values('price_range')

# Create an interactive bar chart using Plotly with pastel colors
fig = px.bar(
    price_distribution, 
    x='price_range', 
    y='count',
    title="Number of Purchases by Price Range",
    labels={'price_range': 'Price Range', 'count': 'Number of Purchases'},
    color='price_range',  # Color by category
    color_discrete_sequence=px.colors.qualitative.Pastel 
)

# Display the chart
fig.show()

The most purchased products in this dataset are those priced between $20 and $90. Products with a price above $1,000 represent a minority in the data.

In [121]:
# Calculate the 99th percentile to remove extreme outliers
price_99 = np.percentile(df_ec_clean['price'], 99)

# Filter the dataset to exclude extreme values
df_filtered = df_ec_clean[df_ec_clean['price'] <= price_99]

fig = px.box(
    df_filtered, 
    y='price', 
    title="Price Distribution (Without Extreme Outliers)", 
    labels={'price': 'Price'},
    color_discrete_sequence=['#FFB6C1'] 
)

# Show the plot
fig.show()


As category code column is really important because of its information, I will drope the null values from it. 

In [125]:
df_ec_clean.info()

<class 'pandas.core.frame.DataFrame'>
Index: 562862 entries, 0 to 2633520
Data columns (total 11 columns):
 #   Column         Non-Null Count   Dtype         
---  ------         --------------   -----         
 0   event_time     562862 non-null  datetime64[ns]
 1   order_id       562862 non-null  int64         
 2   product_id     562862 non-null  int64         
 3   category_id    562862 non-null  float64       
 4   category_code  433938 non-null  object        
 5   brand          535699 non-null  object        
 6   price          562862 non-null  float64       
 7   user_id        562862 non-null  float64       
 8   event_year     562862 non-null  object        
 9   year_month     562862 non-null  period[M]     
 10  price_range    562862 non-null  category      
dtypes: category(1), datetime64[ns](1), float64(3), int64(2), object(3), period[M](1)
memory usage: 47.8+ MB


In [127]:
# Dropping null values in category_code
df_ec_clean = df_ec_clean.dropna(subset=['category_code'])

In [128]:
df_ec_clean.info()

<class 'pandas.core.frame.DataFrame'>
Index: 433938 entries, 0 to 2633520
Data columns (total 11 columns):
 #   Column         Non-Null Count   Dtype         
---  ------         --------------   -----         
 0   event_time     433938 non-null  datetime64[ns]
 1   order_id       433938 non-null  int64         
 2   product_id     433938 non-null  int64         
 3   category_id    433938 non-null  float64       
 4   category_code  433938 non-null  object        
 5   brand          419890 non-null  object        
 6   price          433938 non-null  float64       
 7   user_id        433938 non-null  float64       
 8   event_year     433938 non-null  object        
 9   year_month     433938 non-null  period[M]     
 10  price_range    433938 non-null  category      
dtypes: category(1), datetime64[ns](1), float64(3), int64(2), object(3), period[M](1)
memory usage: 36.8+ MB


In [129]:
# Exporting clean df
df_ec_clean.to_csv("./data/clean_df_ec.csv", index=False)

### Amazon Dataset EDA 

In [2]:
df_amz = pd.read_csv('./data/amz.csv')

In [4]:
df_amz.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10002 entries, 0 to 10001
Data columns (total 28 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   Uniq Id                10002 non-null  object 
 1   Product Name           10002 non-null  object 
 2   Brand Name             0 non-null      float64
 3   Asin                   0 non-null      float64
 4   Category               9172 non-null   object 
 5   Upc Ean Code           34 non-null     object 
 6   List Price             0 non-null      float64
 7   Selling Price          9895 non-null   object 
 8   Quantity               0 non-null      float64
 9   Model Number           8230 non-null   object 
 10  About Product          9729 non-null   object 
 11  Product Specification  8370 non-null   object 
 12  Technical Details      9212 non-null   object 
 13  Shipping Weight        8864 non-null   object 
 14  Product Dimensions     479 non-null    object 
 15  Im

In [5]:
df_amz.head(10)

Uniq Id  \
0  4c69b61db1fc16e7013b43fc926e502d   
1  66d49bbed043f5be260fa9f7fbff5957   
2  2c55cae269aebf53838484b0d7dd931a   
3  18018b6bc416dab347b1b7db79994afa   
4  e04b990e95bf73bbe6a3fa09785d7cd0   
5  f8c32a45e507a177992973cf0d46d20c   
6  40d3cd16b41970ae6872e914aecf2c8e   
7  bc178f33a04dbccefa95b165f8b56830   
8  cc2083338a16c3fe2f7895289d2e98fe   
9  69828c5570dcdbd1609216d33fbad0db   

                                        Product Name  Brand Name  Asin  \
0  DB Longboards CoreFlex Crossbow 41" Bamboo Fib...         NaN   NaN   
1  Electronic Snap Circuits Mini Kits Classpack, ...         NaN   NaN   
2  3Doodler Create Flexy 3D Printing Filament Ref...         NaN   NaN   
3  Guillow Airplane Design Studio with Travel Cas...         NaN   NaN   
4                   Woodstock- Collage 500 pc Puzzle         NaN   NaN   
5  Terra by Battat – 4 Dinosaur Toys, Medium – Di...         NaN   NaN   
6  Rubie's Child's Pokemon Deluxe Pikachu Costume...         NaN   NaN   
7  Hoffmaster 120813 Double-Tipped Triangular Cra...         NaN   NaN   
8  ARTSCAPE Etched Glass 24" x 36" Window Film, 2...         NaN   NaN   
9  Pokemon TCG: Sun and Moon Crimson Invasion Eli...         NaN   NaN   

                                            Category Upc Ean Code  List Price  \
0  Sports & Outdoors | Outdoor Recreation | Skate...          NaN         NaN   
1  Toys & Games | Learning & Education | Science ...          NaN         NaN   
2          Toys & Games | Arts & Crafts | Craft Kits          NaN         NaN   
3  Toys & Games | Hobbies | Models & Model Kits |...          NaN         NaN   
4            Toys & Games | Puzzles | Jigsaw Puzzles          NaN         NaN   
5                                                NaN          NaN         NaN   
6  Clothing, Shoes & Jewelry | Costumes & Accesso...          NaN         NaN   
7  Toys & Games | Arts & Crafts | Drawing & Paint...          NaN         NaN   
8  Home & Kitchen | Home Décor | Window Treatment...          NaN         NaN   
9                                                NaN          NaN         NaN   

  Selling Price  Quantity    Model Number  ...  \
0       $237.68       NaN             NaN  ...   
1        $99.95       NaN           55324  ...   
2        $34.99       NaN             NaN  ...   
3        $28.91       NaN             142  ...   
4        $17.49       NaN           62151  ...   
5        $18.66       NaN         AN4054Z  ...   
6        $29.12       NaN      B07BZJM592  ...   
7        $97.68       NaN             NaN  ...   
8        $12.99       NaN         01-0121  ...   
9        $38.49       NaN  820650802607-1  ...   

                                         Product Url Stock Product Details  \
0  https://www.amazon.com/DB-Longboards-CoreFlex-...   NaN             NaN   
1  https://www.amazon.com/Electronic-Circuits-Cla...   NaN             NaN   
2  https://www.amazon.com/3Doodler-Plastic-Innova...   NaN             NaN   
3  https://www.amazon.com/Guillow-Airplane-Design...   NaN             NaN   
4  https://www.amazon.com/Woodstock-Collage-500-p...   NaN             NaN   
5  https://www.amazon.com/Terra-Battat-Dinosaurs-...   NaN             NaN   
6  https://www.amazon.com/Rubies-Deluxe-Pikachu-P...   NaN             NaN   
7  https://www.amazon.com/Hoffmaster-120813-Doubl...   NaN             NaN   
8  https://www.amazon.com/ARTSCAPE-Etched-Glass-W...   NaN             NaN   
9  https://www.amazon.com/Pokemon-TCG-Crimson-Inv...   NaN             NaN   

  Dimensions Color Ingredients Direction To Use  Is Amazon Seller  \
0        NaN   NaN         NaN              NaN                 Y   
1        NaN   NaN         NaN              NaN                 Y   
2        NaN   NaN         NaN              NaN                 Y   
3        NaN   NaN         NaN              NaN                 Y   
4        NaN   NaN         NaN              NaN                 Y   
5        NaN   NaN         NaN              NaN                 Y  

In [7]:
# Nulls percentage for each column 
(df_amz.isnull().sum() / len(df_amz)) * 100

Uniq Id                    0.000000
Product Name               0.000000
Brand Name               100.000000
Asin                     100.000000
Category                   8.298340
Upc Ean Code              99.660068
List Price               100.000000
Selling Price              1.069786
Quantity                 100.000000
Model Number              17.716457
About Product              2.729454
Product Specification     16.316737
Technical Details          7.898420
Shipping Weight           11.377724
Product Dimensions        95.210958
Image                      0.000000
Variants                  75.224955
Sku                      100.000000
Product Url                0.000000
Stock                    100.000000
Product Details          100.000000
Dimensions               100.000000
Color                    100.000000
Ingredients              100.000000
Direction To Use         100.000000
Is Amazon Seller           0.000000
Size Quantity Variant    100.000000
Product Description      100

In [8]:
# Dropping all the columns with 100% null values: 
df_amz = df_amz.dropna(axis=1, how='all')

In [10]:
df_amz.describe(include='all')

Uniq Id                         Product Name  \
count                              10002                                10002   
unique                             10002                                 9930   
top     2bb94aefc3467ed83860e0e2712d5f10  Btswim NFL Pool Noodles (Pack of 3)   
freq                                   1                                    4   

                                                Category  \
count                                               9172   
unique                                               938   
top     Toys & Games | Games & Accessories | Board Games   
freq                                                 284   

                     Upc Ean Code Selling Price Model Number  \
count                          34          9895         8230   
unique                         34          3876         8109   
top     071444764117 735533033354        $19.99            -   
freq                            1           233           35   

                                            About Product  \
count                                                9729   
unique                                               9036   
top     Quality scenery for use on model railway layou...   
freq                                                   23   

                                    Product Specification  \
count                                                8370   
unique                                               8367   
top     Item Weight:         8.5 pounds    |Shipping W...   
freq                                                    2   

                                        Technical Details Shipping Weight  \
count                                                9212            8864   
unique                                               8657             837   
top     Go to your orders and start the return Select ...        1 pounds   
freq                                                  363             408   

              Product Dimensions  \
count                        479   
unique                       458   
top     4.9 x 21.8 x 14.8 inches   
freq                           4   

                                                    Image  \
count                                               10002   
unique                                               9934   
top     https://m.media-amazon.com/images/I/A13usaonut...   
freq                                                   16   

                                                 Variants  \
count                                                2478   
unique                                               2445   
top     https://www.amazon.com/Wildkin-Insulated-Moist...   
freq                                                    3   

                                              Product Url Is Amazon Seller  
count                                               10002            10002  
unique                                              10002                2  
top     https://www.amazon.com/Hasegawa-Ladders-Lucano...                Y  
freq                                                    1             9723

In [11]:
# Nulls percentage for each column 
(df_amz.isnull().sum() / len(df_amz)) * 100

Uniq Id                   0.000000
Product Name              0.000000
Category                  8.298340
Upc Ean Code             99.660068
Selling Price             1.069786
Model Number             17.716457
About Product             2.729454
Product Specification    16.316737
Technical Details         7.898420
Shipping Weight          11.377724
Product Dimensions       95.210958
Image                     0.000000
Variants                 75.224955
Product Url               0.000000
Is Amazon Seller          0.000000
dtype: float64

Takingo into account the null percentages of Product Dimension, Variants and Upc Ean Code, those will be droped too. 

In [ ]:
# Dropping Product Dimension and UPC Ean Code columns
df_amz = df_amz.drop(columns=['Upc Ean Code', 'Product Dimensions', 'Variants'])

In [24]:
df_amz.head(5)

Uniq Id  \
0  4c69b61db1fc16e7013b43fc926e502d   
1  66d49bbed043f5be260fa9f7fbff5957   
2  2c55cae269aebf53838484b0d7dd931a   
3  18018b6bc416dab347b1b7db79994afa   
4  e04b990e95bf73bbe6a3fa09785d7cd0   

                                        Product Name  \
0  DB Longboards CoreFlex Crossbow 41" Bamboo Fib...   
1  Electronic Snap Circuits Mini Kits Classpack, ...   
2  3Doodler Create Flexy 3D Printing Filament Ref...   
3  Guillow Airplane Design Studio with Travel Cas...   
4                   Woodstock- Collage 500 pc Puzzle   

                                            Category Selling Price  \
0  Sports & Outdoors | Outdoor Recreation | Skate...       $237.68   
1  Toys & Games | Learning & Education | Science ...        $99.95   
2          Toys & Games | Arts & Crafts | Craft Kits        $34.99   
3  Toys & Games | Hobbies | Models & Model Kits |...        $28.91   
4            Toys & Games | Puzzles | Jigsaw Puzzles        $17.49   

  Model Number                                      About Product  \
0          NaN  Make sure this fits by entering your model num...   
1        55324  Make sure this fits by entering your model num...   
2          NaN  Make sure this fits by entering your model num...   
3          142  Make 8 different Planes at one time. | Experim...   
4        62151  Make sure this fits by entering your model num...   

                               Product Specification  \
0  Shipping Weight: 10.7 pounds (View shipping ra...   
1  Product Dimensions:         14.7 x 11.1 x 10.2...   
2  ProductDimensions:10.3x3.4x0.8inches|ItemWeigh...   
3  ProductDimensions:3.5x6.2x13inches|ItemWeight:...   
4  ProductDimensions:1.9x8x10inches|ItemWeight:13...   

                                   Technical Details Shipping Weight  \
0                                                NaN     10.7 pounds   
1  The snap circuits mini kits classpack provides...        4 pounds   
2  show up to 2 reviews by default No longer are ...     12.8 ounces   
3  Go to your orders and start the return Select ...     13.4 ounces   
4  show up to 2 reviews by default 100% Officiall...     13.4 ounces   

                                               Image  \
0  https://images-na.ssl-images-amazon.com/images...   
1  https://images-na.ssl-images-amazon.com/images...   
2  https://images-na.ssl-images-amazon.com/images...   
3  https://images-na.ssl-images-amazon.com/images...   
4  https://images-na.ssl-images-amazon.com/images...   

                                         Product Url Is Amazon Seller  
0  https://www.amazon.com/DB-Longboards-CoreFlex-...                Y  
1  https://www.amazon.com/Electronic-Circuits-Cla...                Y  
2  https://www.amazon.com/3Doodler-Plastic-Innova...                Y  
3  https://www.amazon.com/Guillow-Airplane-Design...                Y  
4  https://www.amazon.com/Woodstock-Collage-500-p...                Y

Checking over random positions for Product Name, Category, About Product, Technical Details, etc...

In [17]:
df_amz['Product Name'][10]

'Moonlite, 3-Story Bundle for Boys, Includes 3 Story Reels for Use with Storybook Projector'

In [19]:
df_amz['Category'][10]

'Toys & Games | Baby & Toddler Toys'

In [20]:
df_amz['About Product'][10]

"Make sure this fits by entering your model number. | 3 story reels: make reading even more magical with the Moonlite story reels bundle! With 3 story reels included in this set, read adventure-filled tales about Pirates, Dragon and a T-Rex to your little boy any time of day, and enjoy them again and again! | Easy-to-use portable storybook projector: The tales included in this 3-pack come alive with Moonlite! Clip the projector (sold separately) onto your smartphone (not included), slide in one of the set's story reels and project vibrant images onto any surface! Moonlite is lightweight and small enough to carry with you wherever you go. | Develop a love of learning: adored by children and adults, award-winning Moonlite and the story reels create an immersive reading experience that instills a love of learning at a young age. As kids follow along to their favorite stories, they develop their imagination, creativity and language skills. | The Moonlite 3-story bundle makes a great gift f

In [21]:
df_amz['Technical Details'][10]

"Go to your orders and start the return Select the ship method Ship it! | Go to your orders and start the return Select the ship method Ship it! | Create a magical story time experience for your child with moonlit 3-story reels bundle! Add tales about pirates, Dragons and a T-Rex to your Moonlite collection and introduce your little boy to exciting, adventure-filled stories he'll love! With the award-winning Moonlite storybook projector for your smartphone (sold separately) and the story reels included in this set, Enjoy reading how to be a pirate, there was an old Dragon who swallowed a Knight and I'm a T.Rex! Clip the projector onto your smartphone or smart device (not included) and slide in a story reel. Use the free app to read along to beautiful projected illustrations and create a truly immersive reading experience with the in-app sound effects! As your child listens to these exciting stories, they'll develop their language skills, creativity and a love of reading and learning. C

In [22]:
df_amz['Product Specification'][10]

'ProductDimensions:0.8x5x8.2inches|ItemWeight:3.2ounces|ShippingWeight:3.2ounces(Viewshippingratesandpolicies)|ASIN:B07NPJNZ9T|Itemmodelnumber:6054517|Manufacturerrecommendedage:36months-5years'

In [25]:
# Number of unique values 
df_amz.nunique()

Uniq Id                  10002
Product Name              9930
Category                   938
Selling Price             3876
Model Number              8109
About Product             9036
Product Specification     8367
Technical Details         8657
Shipping Weight            837
Image                     9934
Product Url              10002
Is Amazon Seller             2
dtype: int64

In [29]:
# Count the frequency of each category and get the top 20 most used
top_20 = df_amz['Category'].value_counts().nlargest(20).reset_index()
top_20.columns = ['Category', 'count']  # Rename columns for clarity

# Create the bar chart
fig = px.bar(top_20, x='Category', y='count', title='Top 20 Most Used Categories',
             color_discrete_sequence=['#40E0D0'])


# Display the chart
fig.show()

Category seems to be the right column to associate this dataset with the ecommerce one. I will drope all of the register that do not have a category associated, as the percentage is about an 8%.

In [31]:
# Dropping null Category values
df_amz = df_amz.dropna(subset=['Category'])


In [32]:
df_amz.info()

<class 'pandas.core.frame.DataFrame'>
Index: 9172 entries, 0 to 10001
Data columns (total 12 columns):
 #   Column                 Non-Null Count  Dtype 
---  ------                 --------------  ----- 
 0   Uniq Id                9172 non-null   object
 1   Product Name           9172 non-null   object
 2   Category               9172 non-null   object
 3   Selling Price          9066 non-null   object
 4   Model Number           7495 non-null   object
 5   About Product          8920 non-null   object
 6   Product Specification  7602 non-null   object
 7   Technical Details      8419 non-null   object
 8   Shipping Weight        8071 non-null   object
 9   Image                  9172 non-null   object
 10  Product Url            9172 non-null   object
 11  Is Amazon Seller       9172 non-null   object
dtypes: object(12)
memory usage: 931.5+ KB


In [ ]:
# Selling Price column analysis
df_amz['Selling Price'].describe()

count       9066
unique      3678
top       $19.99
freq         216
Name: Selling Price, dtype: object

In [36]:
# Convert 'Selling Price' to numeric by removing '$' and converting to float
df_amz['Selling Price'] = df_amz['Selling Price'].replace('[\$,]', '', regex=True).astype(float)

# Create a histogram to visualize price distribution
fig = px.histogram(df_amz, x='Selling Price', title='Selling Price Distribution', nbins=50,
                   color_discrete_sequence=['#40E0D0']) 

# Show the plot
fig.show()

ValueError: could not convert string to float: '74.99 - 249.99'

It seems there are range prices in the selling price column. I will create an extra column to handle it. There are also values that are not only separated by '-'

In [40]:
# Ensure the column is treated as string
df_amz['Selling Price'] = df_amz['Selling Price'].astype(str)

# Identify if the price contains a range (multiple values separated by spaces)
df_amz['has_range'] = df_amz['Selling Price'].str.contains(' ', regex=True, na=False)

# Extract only the first value before the first space
df_amz['Selling Price'] = df_amz['Selling Price'].str.split(' ').str[0]

# Remove non-numeric characters (like '$')
df_amz['Selling Price'] = df_amz['Selling Price'].str.replace('[^\d.]', '', regex=True)

# Convert to numeric
df_amz['Selling Price'] = pd.to_numeric(df_amz['Selling Price'], errors='coerce')

# Verify the changes
print(df_amz[['Selling Price', 'has_range']].head())


   Selling Price  has_range
0         237.68      False
1          99.95      False
2          34.99      False
3          28.91      False
4          17.49      False


In [41]:
df_amz.info()

<class 'pandas.core.frame.DataFrame'>
Index: 9172 entries, 0 to 10001
Data columns (total 13 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   Uniq Id                9172 non-null   object 
 1   Product Name           9172 non-null   object 
 2   Category               9172 non-null   object 
 3   Selling Price          9007 non-null   float64
 4   Model Number           7495 non-null   object 
 5   About Product          8920 non-null   object 
 6   Product Specification  7602 non-null   object 
 7   Technical Details      8419 non-null   object 
 8   Shipping Weight        8071 non-null   object 
 9   Image                  9172 non-null   object 
 10  Product Url            9172 non-null   object 
 11  Is Amazon Seller       9172 non-null   object 
 12  has_range              9172 non-null   bool   
dtypes: bool(1), float64(1), object(11)
memory usage: 940.5+ KB


In [42]:
# Dropping null values in Selling Price as it is not useful to recommend a product without its price
df_amz = df_amz.dropna(subset=['Selling Price'])

In [47]:
# Define price bins based on the data distribution
bins = [0, 10, 17, 30, 100, 500, 1000, 2000, df_amz['Selling Price'].max()]
labels = ['0-10', '10-17', '17-30', '30-100', '100-500', '500-1000', '1000-2000', '2000+']

# Create a new column with price categories
df_amz['price_range'] = pd.cut(df_amz['Selling Price'], bins=bins, labels=labels, right=False)

# Count occurrences of each price range
price_counts = df_amz['price_range'].value_counts().sort_index()

# Create a bar chart with turquoise color
fig = px.bar(price_counts, x=price_counts.index, y=price_counts.values, 
             title='Product Count by Price Range ($)', labels={'x': 'Price Range', 'y': 'Count'},
             color_discrete_sequence=['#40E0D0']) 

# Show the plot
fig.show()


In [49]:
# Selling Price Boxplot
fig = px.box(df_amz, y='Selling Price', 
             title='Overall Price Distribution',
             labels={'Selling Price': 'Price'},
             color_discrete_sequence=['#40E0D0'])  # Turquesa

fig.show()

75% of the products prices are between $0.01 and $30. The maximum price is $5332.

In [52]:
df_amz['Model Number'].nunique()

7265

In [53]:
df_amz.info()

<class 'pandas.core.frame.DataFrame'>
Index: 9007 entries, 0 to 10001
Data columns (total 14 columns):
 #   Column                 Non-Null Count  Dtype   
---  ------                 --------------  -----   
 0   Uniq Id                9007 non-null   object  
 1   Product Name           9007 non-null   object  
 2   Category               9007 non-null   object  
 3   Selling Price          9007 non-null   float64 
 4   Model Number           7347 non-null   object  
 5   About Product          8766 non-null   object  
 6   Product Specification  7446 non-null   object  
 7   Technical Details      8268 non-null   object  
 8   Shipping Weight        7920 non-null   object  
 9   Image                  9007 non-null   object  
 10  Product Url            9007 non-null   object  
 11  Is Amazon Seller       9007 non-null   object  
 12  has_range              9007 non-null   bool    
 13  price_range            9006 non-null   category
dtypes: bool(1), category(1), float64(1), object(

Columns as Uniq Id, Shipping Weight and Model Number are specific to each register, and are not useful in this process. 

In [58]:
# Dropping Product Id and Model Number
df_amz = df_amz.drop(columns=['Uniq Id', 'Shipping Weight', 'Model Number'])

In [59]:
df_amz.info()

<class 'pandas.core.frame.DataFrame'>
Index: 9007 entries, 0 to 10001
Data columns (total 11 columns):
 #   Column                 Non-Null Count  Dtype   
---  ------                 --------------  -----   
 0   Product Name           9007 non-null   object  
 1   Category               9007 non-null   object  
 2   Selling Price          9007 non-null   float64 
 3   About Product          8766 non-null   object  
 4   Product Specification  7446 non-null   object  
 5   Technical Details      8268 non-null   object  
 6   Image                  9007 non-null   object  
 7   Product Url            9007 non-null   object  
 8   Is Amazon Seller       9007 non-null   object  
 9   has_range              9007 non-null   bool    
 10  price_range            9006 non-null   category
dtypes: bool(1), category(1), float64(1), object(8)
memory usage: 721.6+ KB


Assuming the recomendation system will be located in Amazon, the algorythm does not need products from other sellers, so I will drop those ones. 

In [67]:
# Unique values 
df_amz['Is Amazon Seller'].unique()

array(['Y', 'N'], dtype=object)

In [ ]:
# Amount of Yes and No
df_amz['Is Amazon Seller'].value_counts().unique()

array([8820,  187])

In [68]:
# Filtering only Yes
df_amz = df_amz[df_amz['Is Amazon Seller'] != 'N']

In [70]:
df_amz.info()

<class 'pandas.core.frame.DataFrame'>
Index: 8820 entries, 0 to 10001
Data columns (total 11 columns):
 #   Column                 Non-Null Count  Dtype   
---  ------                 --------------  -----   
 0   Product Name           8820 non-null   object  
 1   Category               8820 non-null   object  
 2   Selling Price          8820 non-null   float64 
 3   About Product          8596 non-null   object  
 4   Product Specification  7277 non-null   object  
 5   Technical Details      8111 non-null   object  
 6   Image                  8820 non-null   object  
 7   Product Url            8820 non-null   object  
 8   Is Amazon Seller       8820 non-null   object  
 9   has_range              8820 non-null   bool    
 10  price_range            8819 non-null   category
dtypes: bool(1), category(1), float64(1), object(8)
memory usage: 706.6+ KB


In [71]:
# Dropping Is Amazon Seller column as it is not useful in the algortyhm 
df_amz = df_amz.drop(columns=['Is Amazon Seller'])

In [72]:
# Exporting clean Amazon dataset
df_amz.to_csv("./data/clean_df_amz.csv", index=False)